# Unified Attention Deformable DETR

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## DETR

In [ ]:
# Let's see what is in the model files.

import torch
model_hub = torch.hub.load('facebookresearch/detr', 'detr_resnet50', pretrained=True)
model_hub.eval()

!wget https://dl.fbaipublicfiles.com/detr/detr-r50-e632da11.pth
model_pth = torch.load("/content/detr-r50-e632da11.pth")

Using cache found in /root/.cache/torch/hub/facebookresearch_detr_main


--2023-04-17 20:06:59--  https://dl.fbaipublicfiles.com/detr/detr-r50-e632da11.pth
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 13.35.7.128, 13.35.7.82, 13.35.7.50, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|13.35.7.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 166618694 (159M) [application/octet-stream]
Saving to: ‘detr-r50-e632da11.pth.1’

detr-r50-e632da11.p 100%[===================>] 158.90M   103MB/s    in 1.5s    

2023-04-17 20:07:01 (103 MB/s) - ‘detr-r50-e632da11.pth.1’ saved [166618694/166618694]



In [ ]:
!pip install torchinfo
import torchinfo

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
print(type(model_hub))
print(type(model_pth))

<class 'models.detr.DETR'>
<class 'dict'>


In [ ]:
model_pth['model'].keys()

odict_keys(['transformer.encoder.layers.0.self_attn.in_proj_weight', 'transformer.encoder.layers.0.self_attn.in_proj_bias', 'transformer.encoder.layers.0.self_attn.out_proj.weight', 'transformer.encoder.layers.0.self_attn.out_proj.bias', 'transformer.encoder.layers.0.linear1.weight', 'transformer.encoder.layers.0.linear1.bias', 'transformer.encoder.layers.0.linear2.weight', 'transformer.encoder.layers.0.linear2.bias', 'transformer.encoder.layers.0.norm1.weight', 'transformer.encoder.layers.0.norm1.bias', 'transformer.encoder.layers.0.norm2.weight', 'transformer.encoder.layers.0.norm2.bias', 'transformer.encoder.layers.1.self_attn.in_proj_weight', 'transformer.encoder.layers.1.self_attn.in_proj_bias', 'transformer.encoder.layers.1.self_attn.out_proj.weight', 'transformer.encoder.layers.1.self_attn.out_proj.bias', 'transformer.encoder.layers.1.linear1.weight', 'transformer.encoder.layers.1.linear1.bias', 'transformer.encoder.layers.1.linear2.weight', 'transformer.encoder.layers.1.linear2

In [ ]:
model_hub

DETR(
  (transformer): Transformer(
    (encoder): TransformerEncoder(
      (layers): ModuleList(
        (0-5): 6 x TransformerEncoderLayer(
          (self_attn): MultiheadAttention(
            (out_proj): NonDynamicallyQuantizableLinear(in_features=256, out_features=256, bias=True)
          )
          (linear1): Linear(in_features=256, out_features=2048, bias=True)
          (dropout): Dropout(p=0.1, inplace=False)
          (linear2): Linear(in_features=2048, out_features=256, bias=True)
          (norm1): LayerNorm((256,), eps=1e-05, elementwise_affine=True)
          (norm2): LayerNorm((256,), eps=1e-05, elementwise_affine=True)
          (dropout1): Dropout(p=0.1, inplace=False)
          (dropout2): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (decoder): TransformerDecoder(
      (layers): ModuleList(
        (0-5): 6 x TransformerDecoderLayer(
          (self_attn): MultiheadAttention(
            (out_proj): NonDynamicallyQuantizableLinear(in_features=256, ou

In [ ]:
torchinfo.summary(model_hub)

Layer (type:depth-idx)                                                 Param #
DETR                                                                   --
├─Transformer: 1-1                                                     --
│    └─TransformerEncoder: 2-1                                         --
│    │    └─ModuleList: 3-1                                            7,890,432
│    └─TransformerDecoder: 2-2                                         --
│    │    └─ModuleList: 3-2                                            9,472,512
│    │    └─LayerNorm: 3-3                                             512
├─Linear: 1-2                                                          23,644
├─MLP: 1-3                                                             --
│    └─ModuleList: 2-3                                                 --
│    │    └─Linear: 3-4                                                65,792
│    │    └─Linear: 3-5                                                65,792
│    │

## Environment Setup

In [ ]:
import torch
model = torch.load('/content/UADD/exps/r50_deformable_detr/model_state_dict.pth')

### GPU

In [ ]:
!wget https://developer.nvidia.com/compute/cuda/9.2/Prod2/local_installers/cuda-repo-ubuntu1604-9-2-local_9.2.148-1_amd64

--2023-03-23 19:47:05--  https://developer.nvidia.com/compute/cuda/9.2/Prod2/local_installers/cuda-repo-ubuntu1604-9-2-local_9.2.148-1_amd64
Resolving developer.nvidia.com (developer.nvidia.com)... 152.199.20.126
Connecting to developer.nvidia.com (developer.nvidia.com)|152.199.20.126|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://developer.nvidia.com/downloads/compute/cuda/9.2/Prod2/local_installers/cuda-repo-ubuntu1604-9-2-local_9.2.148-1_amd64 [following]
--2023-03-23 19:47:05--  https://developer.nvidia.com/downloads/compute/cuda/9.2/Prod2/local_installers/cuda-repo-ubuntu1604-9-2-local_9.2.148-1_amd64
Reusing existing connection to developer.nvidia.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://developer.download.nvidia.com/compute/cuda/9.2/secure/Prod2/local_installers/cuda-repo-ubuntu1604-9-2-local_9.2.148-1_amd64.deb?6I9j3r4BXugAy5cYBH1VS0bNaR6N_K8ScI6Ct9eG3fp6p2HC0udluwI7J5H3Wk1ZkQBm5ARGMY_AQfdev

In [ ]:
!dpkg -i /content/cuda-repo-ubuntu1604–9–2-local_9.2.88–1_amd64.deb

(Reading database ... 128358 files and directories currently installed.)
Preparing to unpack .../cuda-repo-ubuntu1604–9–2-local_9.2.88–1_amd64.deb ...
Unpacking cuda-repo-ubuntu1604-9-2-local (9.2.88-1) over (9.2.88-1) ...
Setting up cuda-repo-ubuntu1604-9-2-local (9.2.88-1) ...

The public CUDA GPG key does not appear to be installed.
To install the key, run this command:
sudo apt-key add /var/cuda-repo-9-2-local/7fa2af80.pub



In [ ]:
!apt-key add /var/cuda-repo-9-2-local/7fa2af80.pub

OK


In [ ]:
!apt-get update

Get:1 file:/var/cuda-repo-9-2-local  InRelease
Ign:1 file:/var/cuda-repo-9-2-local  InRelease
Get:2 file:/var/cuda-repo-9-2-local  Release [574 B]
Get:2 file:/var/cuda-repo-9-2-local  Release [574 B]
Get:3 file:/var/cuda-repo-9-2-local  Release.gpg [819 B]
Get:3 file:/var/cuda-repo-9-2-local  Release.gpg [819 B]
Hit:4 http://archive.ubuntu.com/ubuntu focal InRelease
Hit:5 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu focal InRelease
Hit:6 http://archive.ubuntu.com/ubuntu focal-updates InRelease
Hit:7 http://archive.ubuntu.com/ubuntu focal-backports InRelease
Hit:8 http://ppa.launchpad.net/cran/libgit2/ubuntu focal InRelease
Hit:9 https://cloud.r-project.org/bin/linux/ubuntu focal-cran40/ InRelease
Hit:10 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu focal InRelease
Hit:11 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu focal InRelease
Hit:12 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2004/x86_64  InRelease
Hit:13 http://ppa.launchpad.net/ubuntugis/ppa/u

In [ ]:
!apt-get install cuda=9.2.88-1

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  cuda-9-2 cuda-command-line-tools-9-2 cuda-compiler-9-2 cuda-cublas-9-2
  cuda-cublas-dev-9-2 cuda-cudart-9-2 cuda-cudart-dev-9-2 cuda-cufft-9-2
  cuda-cufft-dev-9-2 cuda-cuobjdump-9-2 cuda-cupti-9-2 cuda-curand-9-2
  cuda-curand-dev-9-2 cuda-cusolver-9-2 cuda-cusolver-dev-9-2
  cuda-cusparse-9-2 cuda-cusparse-dev-9-2 cuda-demo-suite-9-2
  cuda-documentation-9-2 cuda-driver-dev-9-2 cuda-gdb-9-2
  cuda-gpu-library-advisor-9-2 cuda-libraries-9-2 cuda-libraries-dev-9-2
  cuda-license-9-2 cuda-memcheck-9-2 cuda-misc-headers-9-2 cuda-npp-9-2
  cuda-npp-dev-9-2 cuda-nsight-9-2 cuda-nvcc-9-2 cuda-nvdisasm-9-2
  cuda-nvgraph-9-2 cuda-nvgraph-dev-9-2 cuda-nvml-dev-9-2 cuda-nvprof-9-2
  cuda-nvprune-9-2 cuda-nvrtc-9-2 cuda-nvrtc-dev-9-2 cuda-nvtx-9-2
  cuda-nvvp-9-2 cuda-runtime-9-2 cuda-samples-9-2 cuda-toolkit-9-2
  cuda-tools-9-2 cuda-visual-too

In [ ]:
!rm -rf /usr/local/cuda
!ln -s /usr/local/cuda-9.2 /usr/local/cuda

In [ ]:
!nvcc -V

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2018 NVIDIA Corporation
Built on Wed_Apr_11_23:16:29_CDT_2018
Cuda compilation tools, release 9.2, V9.2.88


In [ ]:
!nvcc -V
!gcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2018 NVIDIA Corporation
Built on Wed_Apr_11_23:16:29_CDT_2018
Cuda compilation tools, release 9.2, V9.2.88
gcc (Ubuntu 9.4.0-1ubuntu1~20.04.1) 9.4.0
Copyright (C) 2019 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.



### Conda

In [ ]:
%env PYTHONPATH=

env: PYTHONPATH=


In [ ]:
! wget https://repo.anaconda.com/miniconda/Miniconda3-py37_23.1.0-1-Linux-x86_64.sh
! chmod +x Miniconda3-py37_23.1.0-1-Linux-x86_64.sh
! bash ./Miniconda3-py37_23.1.0-1-Linux-x86_64.sh -b -f -p /usr/local
import sys
sys.path.append('/usr/local/lib/python3.7/site-packages/')

--2023-03-23 20:10:44--  https://repo.anaconda.com/miniconda/Miniconda3-py37_23.1.0-1-Linux-x86_64.sh
Resolving repo.anaconda.com (repo.anaconda.com)... 104.16.130.3, 104.16.131.3, 2606:4700::6810:8303, ...
Connecting to repo.anaconda.com (repo.anaconda.com)|104.16.130.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 90665082 (86M) [application/x-sh]
Saving to: ‘Miniconda3-py37_23.1.0-1-Linux-x86_64.sh’

Miniconda3-py37_23. 100%[===================>]  86.46M   151MB/s    in 0.6s    

2023-03-23 20:10:45 (151 MB/s) - ‘Miniconda3-py37_23.1.0-1-Linux-x86_64.sh’ saved [90665082/90665082]

PREFIX=/usr/local
Unpacking payload ...
                                                                                      
Installing base environment...





Preparing transaction: - \ | / - \ done
Executing transaction: / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ done
installation finished.


In [ ]:
!conda install pytorch=1.5.1 torchvision=0.6.1 cudatoolkit=9.2 -c pytorch -y

Solving environment: / failed with initial frozen solve. Retrying with flexible solve.
Solving environment: \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / done

## Package Plan ##

  environment location: /usr/local

  added / updated specs:
    - cudatoolkit=9.2
    - pytorch=1.5.1
    - torchvision=0.6.1


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    blas-1.0                   |              mkl           6 KB
    cudatoolkit-9.2            |                0       233.9 MB
    freetype-2.12.1            |       h4a9f257_0         626 KB
    giflib-5.2.1               |       h5eee18b_3          80 KB
    intel-openmp-2021.4.0      |    h06a4308_3561         4.2 MB
    jpeg-9e                   

In [ ]:
!conda info


     active environment : None
       user config file : /root/.condarc
 populated config files : 
          conda version : 23.1.0
    conda-build version : not installed
         python version : 3.7.16.final.0
       virtual packages : __archspec=1=x86_64
                          __cuda=12.0=0
                          __glibc=2.31=0
                          __linux=5.10.147=0
                          __unix=0=0
       base environment : /usr/local  (writable)
      conda av data dir : /usr/local/etc/conda
  conda av metadata url : None
           channel URLs : https://repo.anaconda.com/pkgs/main/linux-64
                          https://repo.anaconda.com/pkgs/main/noarch
                          https://repo.anaconda.com/pkgs/r/linux-64
                          https://repo.anaconda.com/pkgs/r/noarch
          package cache : /usr/local/pkgs
                          /root/.conda/pkgs
       envs directories : /usr/local/envs
                          /root/.conda/envs
    

In [ ]:
!conda list

# packages in environment at /usr/local:
#
# Name                    Version                   Build  Channel
_libgcc_mutex             0.1                        main  
_openmp_mutex             5.1                       1_gnu  
blas                      1.0                         mkl  
brotlipy                  0.7.0           py37h27cfd23_1003  
ca-certificates           2023.01.10           h06a4308_0  
certifi                   2022.12.7        py37h06a4308_0  
cffi                      1.15.1           py37h5eee18b_3  
charset-normalizer        2.0.4              pyhd3eb1b0_0  
conda                     23.1.0           py37h06a4308_0  
conda-content-trust       0.1.3            py37h06a4308_0  
conda-package-handling    2.0.2            py37h06a4308_0  
conda-package-streaming   0.7.0            py37h06a4308_0  
cryptography              38.0.4           py37h9ce1e76_0  
cudatoolkit               9.2                           0  
flit-core                 3.6.0              pyh

### Code Repository

#### UADD

In [ ]:
# BEFORE DELETING REPO, SAVE THE DATA!
!mv /content/UADD/data /content/

In [ ]:
!mv /content/data/ /content/UADD/

In [1]:
%cd /content/

# delete previous version
!rm -rf UADD

# get new version
!git clone https://github.com/chrisindris/UADD.git

/content
Cloning into 'UADD'...
remote: Enumerating objects: 382, done.
remote: Counting objects: 100% (308/308), done.
remote: Compressing objects: 100% (168/168), done.
remote: Total 382 (delta 160), reused 259 (delta 134), pack-reused 74
Receiving objects: 100% (382/382), 1.50 MiB | 3.10 MiB/s, done.
Resolving deltas: 100% (182/182), done.


In [2]:
%cd UADD
!pip install -r requirements.txt # other requirements; may need to restart runtime
!pip install -r /content/UADD/ECANet/requirements.txt

/content/UADD
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
%cd /content/UADD/models/ops
!sh ./make.sh
# unit test (should see all checking is True)
#!python test.py

/content/UADD/models/ops
running build
running build_py
creating build
creating build/lib.linux-x86_64-3.10
creating build/lib.linux-x86_64-3.10/modules
copying modules/__init__.py -> build/lib.linux-x86_64-3.10/modules
copying modules/ms_deform_attn.py -> build/lib.linux-x86_64-3.10/modules
creating build/lib.linux-x86_64-3.10/functions
copying functions/__init__.py -> build/lib.linux-x86_64-3.10/functions
copying functions/ms_deform_attn_func.py -> build/lib.linux-x86_64-3.10/functions
running build_ext
/usr/local/lib/python3.10/dist-packages/torch/utils/cpp_extension.py:476: UserWarning: Attempted to use ninja as the BuildExtension backend but we could not find ninja.. Falling back to using the slow distutils backend.
  warnings.warn(msg.format('we could not find ninja.'))
/usr/local/lib/python3.10/dist-packages/torch/utils/cpp_extension.py:398: UserWarning: There are no x86_64-linux-gnu-g++ version bounds defined for CUDA version 11.8
  warnings.warn(f'There are no {compiler_name} 

In [4]:
# Get the dataset
%mkdir /content/UADD/data/
%mkdir /content/UADD/data/coco/

%cd /content/UADD/data/coco/
!wget http://images.cocodataset.org/zips/train2017.zip
!wget http://images.cocodataset.org/zips/val2017.zip
!wget http://images.cocodataset.org/annotations/annotations_trainval2017.zip

%cd /content/UADD/data/coco/
!unzip train2017.zip
!unzip val2017.zip
!unzip annotations_trainval2017.zip

Streaming output truncated to the last 5000 lines.
 extracting: val2017/000000365745.jpg  
 extracting: val2017/000000320425.jpg  
 extracting: val2017/000000481404.jpg  
 extracting: val2017/000000314294.jpg  
 extracting: val2017/000000335328.jpg  
 extracting: val2017/000000513688.jpg  
 extracting: val2017/000000158548.jpg  
 extracting: val2017/000000132116.jpg  
 extracting: val2017/000000415238.jpg  
 extracting: val2017/000000321333.jpg  
 extracting: val2017/000000081738.jpg  
 extracting: val2017/000000577584.jpg  
 extracting: val2017/000000346905.jpg  
 extracting: val2017/000000433980.jpg  
 extracting: val2017/000000228144.jpg  
 extracting: val2017/000000041872.jpg  
 extracting: val2017/000000117492.jpg  
 extracting: val2017/000000368900.jpg  
 extracting: val2017/000000376900.jpg  
 extracting: val2017/000000352491.jpg  
 extracting: val2017/000000330790.jpg  
 extracting: val2017/000000384850.jpg  
 extracting: val2017/000000032735.jpg  
 extracting: val2017/00000019

##### UADD-default (DefDETR)

In [ ]:
%cd /content/UADD/

# run the normal DefDETR
!GPUS_PER_NODE=1 ./tools/run_dist_launch.sh 1 ./configs/r50_deformable_detr.sh

/content/UADD
+ GPUS=1
+ RUN_COMMAND=./configs/r50_deformable_detr.sh
+ '[' 1 -lt 8 ']'
+ GPUS_PER_NODE=1
+ MASTER_ADDR=127.0.0.1
+ MASTER_PORT=29500
+ NODE_RANK=0
+ let NNODES=GPUS/GPUS_PER_NODE
+ python ./tools/launch.py --nnodes 1 --node_rank 0 --master_addr 127.0.0.1 --master_port 29500 --nproc_per_node 1 ./configs/r50_deformable_detr.sh
+ EXP_DIR=exps/r50_deformable_detr
+ PY_ARGS=
+ python -u main.py --output_dir exps/r50_deformable_detr
| distributed init (rank 0): env://
git:
  sha: 6cf1aca12da303f7532ba8256acb51e4e6679dc1, status: clean, branch: main

Namespace(lr=0.0002, lr_backbone_names=['backbone.0'], lr_backbone=2e-05, lr_linear_proj_names=['reference_points', 'sampling_offsets'], lr_linear_proj_mult=0.1, batch_size=2, weight_decay=0.0001, epochs=1, lr_drop=40, lr_drop_epochs=None, clip_max_norm=0.1, sgd=False, with_box_refine=False, two_stage=False, frozen_weights=None, backbone='resnet50', dilation=False, position_embedding='sine', position_embedding_scale=6.28318530717

##### UADD with ECA-Net

In [5]:
%cd /content/UADD/

# run the DefDETR with ECA backbone
!GPUS_PER_NODE=1 ./tools/run_dist_launch.sh 1 ./configs/eca_deformable_detr.sh

Streaming output truncated to the last 5000 lines.
Epoch: [1]  [23330/59143]  eta: 2:28:22  lr: 0.000200  class_error: 87.50  grad_norm: 120.95  loss: 23.2427 (23.3672)  loss_ce: 1.5716 (1.7032)  loss_bbox: 0.8997 (0.9225)  loss_giou: 1.1730 (1.2377)  loss_ce_0: 1.6390 (1.7084)  loss_bbox_0: 0.9447 (0.9465)  loss_giou_0: 1.2931 (1.2520)  loss_ce_1: 1.6098 (1.7135)  loss_bbox_1: 0.9467 (0.9591)  loss_giou_1: 1.2209 (1.2619)  loss_ce_2: 1.6686 (1.7131)  loss_bbox_2: 0.8728 (0.9315)  loss_giou_2: 1.1939 (1.2461)  loss_ce_3: 1.6017 (1.7108)  loss_bbox_3: 0.9450 (0.9339)  loss_giou_3: 1.1824 (1.2455)  loss_ce_4: 1.6441 (1.7063)  loss_bbox_4: 0.9455 (0.9332)  loss_giou_4: 1.2184 (1.2420)  loss_ce_unscaled: 0.7858 (0.8516)  class_error_unscaled: 66.6667 (72.5165)  loss_bbox_unscaled: 0.1799 (0.1845)  loss_giou_unscaled: 0.5865 (0.6189)  cardinality_error_unscaled: 294.5000 (293.4150)  loss_ce_0_unscaled: 0.8195 (0.8542)  loss_bbox_0_unscaled: 0.1889 (0.1893)  loss_giou_0_unscaled: 0.6465 (0.6

#### ECANet

In [ ]:
# later, we add to UADD
%cd /content/UADD/

# delete previous version
!rm -rf /content/UADD/ECANet

# get new version
!git clone https://github.com/chrisindris/ECANet.git
!pip install -r /content/UADD/ECANet/requirements.txt

/content/UADD
Cloning into 'ECANet'...
remote: Enumerating objects: 119, done.
remote: Counting objects: 100% (18/18), done.
remote: Compressing objects: 100% (12/12), done.
remote: Total 119 (delta 7), reused 15 (delta 5), pack-reused 101
Receiving objects: 100% (119/119), 1.08 MiB | 986.00 KiB/s, done.
Resolving deltas: 100% (55/55), done.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!python /content/ECANet/main.py -a eca_resnet50 --ksize 3557 /content/data

=> creating model 'eca_resnet50'
Constructing eca_resnet50......
DataParallel(
  (module): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): ECABottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
       

# Old Setup

In [ ]:
! wget https://repo.anaconda.com/miniconda/Miniconda3-py37_4.8.2-Linux-x86_64.sh
! chmod +x Miniconda3-py37_4.8.2-Linux-x86_64.sh
! bash ./Miniconda3-py37_4.8.2-Linux-x86_64.sh -b -f -p /usr/local
import sys
sys.path.append('/usr/local/lib/python3.7/site-packages/')

--2023-03-23 18:21:14--  https://repo.anaconda.com/miniconda/Miniconda3-py37_4.8.2-Linux-x86_64.sh
Resolving repo.anaconda.com (repo.anaconda.com)... 104.16.131.3, 104.16.130.3, 2606:4700::6810:8303, ...
Connecting to repo.anaconda.com (repo.anaconda.com)|104.16.131.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 85055499 (81M) [application/x-sh]
Saving to: ‘Miniconda3-py37_4.8.2-Linux-x86_64.sh’

Miniconda3-py37_4.8 100%[===================>]  81.12M  78.2MB/s    in 1.0s    

2023-03-23 18:21:15 (78.2 MB/s) - ‘Miniconda3-py37_4.8.2-Linux-x86_64.sh’ saved [85055499/85055499]

PREFIX=/usr/local
Unpacking payload ...
Solving environment: - \ | / done

## Package Plan ##

  environment location: /usr/local

  added / updated specs:
    - _libgcc_mutex==0.1=main
    - asn1crypto==1.3.0=py37_0
    - ca-certificates==2020.1.1=0
    - certifi==2019.11.28=py37_0
    - cffi==1.14.0=py37h2e261b9_0
    - chardet==3.0.4=py37_1003
    - conda-package-handling==1.

In [ ]:
!conda install pytorch=1.5.1 torchvision=0.6.1 cudatoolkit=9.2 -c pytorch -y

In [ ]:
import torch

In [ ]:
!pip list

Package                Version            
---------------------- -------------------
asn1crypto             1.3.0              
certifi                2022.12.7          
cffi                   1.14.0             
chardet                3.0.4              
conda                  23.1.0             
conda-package-handling 1.6.0              
cryptography           2.8                
flit-core              3.6.0              
idna                   2.8                
importlib-metadata     4.11.3             
mkl-fft                1.3.1              
mkl-random             1.2.2              
mkl-service            2.4.0              
numpy                  1.21.5             
Pillow                 9.0.1              
pip                    20.0.2             
pluggy                 1.0.0              
pycosat                0.6.3              
pycparser              2.19               
pyOpenSSL              19.1.0             
PySocks                1.7.1              
requests   

### Conda

In [ ]:
%env PYTHONPATH=

env: PYTHONPATH=


In [ ]:
%%bash
MINICONDA_INSTALLER_SCRIPT=Miniconda3-py37_23.1.0-1-Linux-x86_64.sh
MINICONDA_PREFIX=/usr/local
wget https://repo.anaconda.com/miniconda/$MINICONDA_INSTALLER_SCRIPT
chmod +x $MINICONDA_INSTALLER_SCRIPT
./$MINICONDA_INSTALLER_SCRIPT -b -f -p $MINICONDA_PREFIX

PREFIX=/usr/local
Unpacking payload ...

Installing base environment...





Preparing transaction: ...working... done
Executing transaction: ...working... done
installation finished.


--2023-03-23 18:04:04--  https://repo.anaconda.com/miniconda/Miniconda3-py37_23.1.0-1-Linux-x86_64.sh
Resolving repo.anaconda.com (repo.anaconda.com)... 104.16.130.3, 104.16.131.3, 2606:4700::6810:8303, ...
Connecting to repo.anaconda.com (repo.anaconda.com)|104.16.130.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 90665082 (86M) [application/x-sh]
Saving to: ‘Miniconda3-py37_23.1.0-1-Linux-x86_64.sh’

     0K .......... .......... .......... .......... ..........  0% 4.43M 19s
    50K .......... .......... .......... .......... ..........  0% 4.51M 19s
   100K .......... .......... .......... .......... ..........  0% 14.5M 15s
   150K .......... .......... .......... .......... ..........  0% 14.7M 13s
   200K .......... .......... .......... .......... ..........  0% 11.6M 12s
   250K .......... .......... .......... .......... ..........  0% 20.5M 10s
   300K .......... .......... .......... .......... ..........  0% 17.9M 10s
   350K .......... .......

In [ ]:
!which conda
!conda --version

/usr/local/bin/conda
conda 23.1.0


In [ ]:
!python --version

Python 3.7.16


In [ ]:
!conda update conda

In [ ]:
%%shell
eval "$(conda shell.bash hook)" # copy conda command to shell
conda activate deformable_detr
conda install pytorch=1.5.1 torchvision=0.6.1 cudatoolkit=9.2 -c pytorch

Solving environment: \ failed with initial frozen solve. Retrying with flexible solve.
Solving environment: - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | 

In [ ]:
%%shell
eval "$(conda shell.bash hook)" # copy conda command to shell
conda activate deformable_detr
python --version
python -c "import torch; print(torch.__version__)"

Python 3.7.12
1.5.1
